In [ ]:
# Based on and corrected from: 
# https://www.esri.com/arcgis-blog/products/arcgis/imagery/precipitation-patterns-and-trends-predictions-multidimensional-data/

import arcpy
from arcpy import env
from arcpy.sa import *

arcpy.env.overwriteOutput = True

# Load NOAA's NetCDF file as multidimensional raster 
precip_raster = arcpy.Raster(r"D:\GIS_Aineistot\Multidimensional_data\NOAA\source_data\precip.mon.total.v501.nc", True) 
# NOTICE: you must replace the folder path to your own!

precip_raster

In [ ]:
# Stretch image symbology range using DRA and display
## DRA stands for Dynamic Range Adjustment, meaning that histogram is stretched based only on the pixel...
## ... values within the display and not using all the pixels in the raster dataset
precip_raster_stretch = arcpy.ia.Stretch(precip_raster, "PercentClip", None, None, None, None, True, 0.25, 0.75, None, None, None)
precip_raster_stretch

In [ ]:
# Save the data as optimized datacube in Cloud Raster Format (CRF)

arcpy.env.parallelProcessingFactor = "50%" # you can also use i.e. '4' here to state you want to designate 4 CPU's for tasks
precip_raster.save(r"D:\GIS_Aineistot\Multidimensional_data\NOAA\precip_test.crf") 
# NOTICE: you must replace the folder path to your own!

# ... saving might take a moment. When you do not see an asterisk(*) on left, the processing is complete.

In [ ]:
# Check the list of variable names and their dimensions
precip_raster.variables

In [ ]:
# Get the time dimension values for the precipitation variable
precip_raster.getDimensionValues("precip", "StdTime")

In [ ]:
## Check if it is multidimensional raster
is_multidimensional = precip_raster.isMultidimensional
is_multidimensional

In [ ]:
## Return the multidimensional information
my_mdinfo = precip_raster.mdinfo
my_mdinfo

In [ ]:
## Return the list of variable names and their dimensions
my_variables = precip_raster.variables
my_variables

In [ ]:
## Get the time dimension values for the precipitation variable
my_dimensionValues = precip_raster.getDimensionValues("precip", "StdTime")
my_dimensionValues

In [ ]:
## Aggregate monthly precipitation to mean annual precipitation; it can be netcdf, grib, HDF, CRF or using MD as source data.

aggMultidim = AggregateMultidimensionalRaster(r"D:\GIS_Aineistot\Multidimensional_data\NOAA\source_data\precip.mon.total.v501.nc", "StdTime", "MEAN", "precip", "INTERVAL_KEYWORD", "YEARLY", "", "", "", "", "DATA")
## NOTICE: You need to update the folder path to your own data folder!

### The Aggregation might take some time...

In [ ]:
# Now save the created raster as CRF dataset
aggMultidim.save(r"D:\GIS_Aineistot\Multidimensional_data\NOAA\aggregate_precip_Yearly.crf")
## NOTICE: You need to update the folder path to your own! You can leave the dataset name and .crf ending.

### EXTRA NOTICE: You should now have the "aggMultidim" raster visible in your Contents pane as a layer. The time slider atop the map is activated...

#### EXTRA^2 NOTICE: You can create 'temporal profile charts' (as in article...) by right-click on layer -> Create Chart -> Temporal Profile.
##### ... To use the Temporal Profile chart, you need to digitize polygons or areas from the 'Chart Properties' pane. Ask instructor for help if necessary.

In [ ]:
# End of instructed Notebook (the workflow continues in the article). Do the rest if time allows it or in your own free time.

In [ ]:
# Anomaly Detection. We compute anomaly for each slice in the multidimensional raster to look at the deviation from mean precipitation.

from arcpy.ia import GenerateMultidimensionalAnomaly
# define input parameters
inputFile = "aggMultidim"
variable = "precip"
averageMethod = "DIFFERENCE_FROM_MEAN"
averageInterval = "ALL"
ignoreNoData = "DATA"

# Execute
yearly_Anomaly = GenerateMultidimensionalAnomaly(inputFile, variable, averageMethod, averageInterval, ignoreNoData)

In [ ]:
# Save results

yearly_Anomaly.save(r"D:\GIS_Aineistot\Multidimensional_data\NOAA\PrecipitationAnomaly.crf")
## NOTICE: You need to update the folder path to your own! You can leave the dataset name and .crf ending.

# Try Time-Slider in ArcGIS Pro... Set the time span to ~1 year.